**Enlace al Notebook del día 4 (primer día con python)**

[![Open In Colab](https://colab.research.google.com/assets/colab-badge.svg)](https://colab.research.google.com/github/Digdgeo/GEE_Course_2022/blob/main/Dia4/SDM_geemap_course_day_4.ipynb)

In [ ]:
#!pip install geemap

# <font color = 'red'>**GEE Lesson 10 - Reducing an Earth Engine ImageCollection**</font>


https://tutorials.geemap.org/ImageCollection/reducing_image_collection/

**Reducing an ImageCollection**

To composite images in an `ImageCollection`, use `imageCollection.reduce()`. This will composite all the images in the collection to a single image representing, for example, the min, max, mean or standard deviation of the images. (See the Reducers section for more information about reducers). For example, to create a median value image from a collection:

In [1]:
import ee
import geemap

ee.Authenticate()
ee.Initialize(project='ee-digdgeografo')

In [2]:
Map = geemap.Map()
Map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

## Compute a median image

In [3]:
# Load a Landsat 8 collection for a single path-row.
collection = ee.ImageCollection('LANDSAT/LC08/C02/T1_L2') \
    .filter(ee.Filter.eq('WRS_PATH', 202)) \
    .filter(ee.Filter.eq('WRS_ROW', 34)) \
    .filterDate('2023-01-01', '2023-12-31')

# Compute a median image and display.
median = collection.median()
Map.setCenter(-6.15, 37, 12)
Map.addLayer(median, {'bands': ['SR_B4',  'SR_B3',  'SR_B2'], 'max': 20000}, 'median')

In [4]:
collection.size().getInfo()

22

In [5]:
collection.aggregate_array("system:id").getInfo()

['LANDSAT/LC08/C02/T1_L2/LC08_202034_20230125',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230210',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230226',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230314',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230330',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230415',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230501',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230517',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230602',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230618',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230704',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230720',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230805',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230821',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230906',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230922',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20231008',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20231024',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20231109',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20231125',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_202

At each location in the output image, in each band, the pixel value is the median of all unmasked pixels in the input imagery (the images in the collection). In the previous example, median() is a convenience method for the following call:

In [7]:
# Reduce the collection with a median reducer.
median = collection.reduce(ee.Reducer.median())

# Display the median image.
Map.addLayer(median,
             {'bands': ['SR_B4_median',  'SR_B3_median',  'SR_B2_median'], 'max': 20000},
             'also median')
Map

Map(bottom=102222.0, center=[37.1230963549893, -6.034283661067098], controls=(WidgetControl(options=['position…

## Create an image composite

In [8]:
peninsula = ee.FeatureCollection('projects/ee-digdgeografo/assets/peninsula_iberica')
#Map.addLayer(peninsula)

In [9]:
collection = ee.ImageCollection('LANDSAT/LC08/C02/T1_L2') \
    .filterBounds(peninsula) \
    .filterDate('2023-01-01', '2023-12-31')

In [10]:
collection.size().getInfo()

983

In [11]:
spain = peninsula.filter(ee.Filter.eq("ADM0_A3", "ESP"))
portugal = peninsula.filter(ee.Filter.eq("ADM0_A3", "PRT"))
#Map.addLayer(portugal, {}, "Portugal")

In [12]:
image = collection.median().clip(spain)
Map.addLayer(image, {'bands': ['SR_B4',  'SR_B3',  'SR_B2'], 'min': 7500, 'max': 20000}, 'Landsat 2023')

#<font color = 'red'>**GEE Lesson 11 - Using the map function with Earth Engine Image Collection**</font>

https://tutorials.geemap.org/ImageCollection/mapping_over_image_collection/

In [13]:
Map = geemap.Map()

In [14]:
def minus1000(num):
    result = ee.Number(num).subtract(1000)
    return result

In [15]:
result = minus1000(2000)
print(result.getInfo())

1000


## Apply the map function

In [16]:
years = ee.List.sequence(2000, 2010)
print(years.getInfo())

[2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010]


In [17]:
results = years.map(minus1000)
print(results.getInfo())

[1000, 1001, 1002, 1003, 1004, 1005, 1006, 1007, 1008, 1009, 1010]


## Use anonymous/lambda function

In [18]:
years = ee.List.sequence(2000, 2010)

results = years.map(lambda x: ee.Number(x).subtract(1000))
print(results.getInfo())

[1000, 1001, 1002, 1003, 1004, 1005, 1006, 1007, 1008, 1009, 1010]


## Filter an ImageCollection

In [19]:
roi = ee.Geometry.Point(-5.92, 36.96)

collection = ee.ImageCollection('LANDSAT/LC08/C02/T1_L2') \
    .filterBounds(roi) \
    .filterDate("2023-01-01", "2024-01-01") \
    .sort("CLOUD_COVER")

print(collection.size().getInfo())

44


In [20]:
image = collection.first()

In [21]:
image.getInfo()

{'type': 'Image',
 'bands': [{'id': 'SR_B1',
   'data_type': {'type': 'PixelType',
    'precision': 'int',
    'min': 0,
    'max': 65535},
   'dimensions': [7571, 7711],
   'crs': 'EPSG:32629',
   'crs_transform': [30, 0, 631485, 0, -30, 4266315]},
  {'id': 'SR_B2',
   'data_type': {'type': 'PixelType',
    'precision': 'int',
    'min': 0,
    'max': 65535},
   'dimensions': [7571, 7711],
   'crs': 'EPSG:32629',
   'crs_transform': [30, 0, 631485, 0, -30, 4266315]},
  {'id': 'SR_B3',
   'data_type': {'type': 'PixelType',
    'precision': 'int',
    'min': 0,
    'max': 65535},
   'dimensions': [7571, 7711],
   'crs': 'EPSG:32629',
   'crs_transform': [30, 0, 631485, 0, -30, 4266315]},
  {'id': 'SR_B4',
   'data_type': {'type': 'PixelType',
    'precision': 'int',
    'min': 0,
    'max': 65535},
   'dimensions': [7571, 7711],
   'crs': 'EPSG:32629',
   'crs_transform': [30, 0, 631485, 0, -30, 4266315]},
  {'id': 'SR_B5',
   'data_type': {'type': 'PixelType',
    'precision': 'int',
 

In [22]:
geemap.image_props(image).getInfo()

{'ALGORITHM_SOURCE_SURFACE_REFLECTANCE': 'LaSRC_1.6.0',
 'ALGORITHM_SOURCE_SURFACE_TEMPERATURE': 'st_1.5.0',
 'CLOUD_COVER': 0,
 'CLOUD_COVER_LAND': 0,
 'COLLECTION_CATEGORY': 'T1',
 'COLLECTION_NUMBER': 2,
 'DATA_SOURCE_AIR_TEMPERATURE': 'MODIS',
 'DATA_SOURCE_ELEVATION': 'GLS2000',
 'DATA_SOURCE_OZONE': 'MODIS',
 'DATA_SOURCE_PRESSURE': 'Calculated',
 'DATA_SOURCE_REANALYSIS': 'GEOS-5 FP-IT',
 'DATA_SOURCE_TIRS_STRAY_LIGHT_CORRECTION': 'TIRS',
 'DATA_SOURCE_WATER_VAPOR': 'MODIS',
 'DATE_ACQUIRED': '2023-08-05',
 'DATE_PRODUCT_GENERATED': 1691803545000,
 'DATUM': 'WGS84',
 'EARTH_SUN_DISTANCE': 1.0144788,
 'ELLIPSOID': 'WGS84',
 'GEOMETRIC_RMSE_MODEL': 6.466,
 'GEOMETRIC_RMSE_MODEL_X': 4.415,
 'GEOMETRIC_RMSE_MODEL_Y': 4.723,
 'GEOMETRIC_RMSE_VERIFY': 3.37,
 'GRID_CELL_SIZE_REFLECTIVE': 30,
 'GRID_CELL_SIZE_THERMAL': 30,
 'GROUND_CONTROL_POINTS_MODEL': 799,
 'GROUND_CONTROL_POINTS_VERIFY': 65,
 'GROUND_CONTROL_POINTS_VERSION': 5,
 'IMAGE_DATE': '2023-08-05',
 'IMAGE_QUALITY_OLI': 9,
 

In [23]:
collection.aggregate_array("CLOUD_COVER").getInfo()

[0,
 0,
 0.01,
 0.03,
 0.04,
 0.06,
 0.07,
 0.11,
 0.19,
 0.2,
 0.23,
 0.51,
 0.76,
 1.1,
 1.13,
 1.78,
 2.34,
 2.65,
 3.13,
 3.47,
 4.48,
 4.72,
 5.99,
 7.35,
 13.26,
 20.98,
 21.08,
 21.16,
 31.76,
 43.01,
 43.61,
 47.69,
 50.8,
 52.44,
 54.59,
 60.18,
 63.13,
 63.36,
 67.74,
 73.6,
 78.4,
 85.83,
 86.55,
 99.65]

In [38]:
#Map = geemap.Map()
vis_params = {
    'bands': ['SR_B5', 'SR_B4', 'SR_B3'],
    'min': 8000,
    'max': 18000
}

Map.addLayer(image, vis_params, "First image")
Map.centerObject(image)
Map

Map(bottom=102810.0, center=[36.80708566272707, -6.19903564453125], controls=(WidgetControl(options=['position…

## Select the best image each year

In [27]:
roi = ee.Geometry.Point(-5.99, 36.96)

def best_image(year):

    start_date = ee.Date.fromYMD(year, 1, 1)
    end_date = start_date.advance(1, 'year')

    image = ee.ImageCollection('LANDSAT/LC08/C02/T1_L2') \
        .filterBounds(roi) \
        .filterDate(start_date, end_date) \
        .sort("CLOUD_COVER") \
        .first()

    return image

In [28]:
start_year = 2013
end_year = 2023
years = ee.List.sequence(start_year, end_year)
year_list = years.getInfo()
print(year_list)

[2013, 2014, 2015, 2016, 2017, 2018, 2019, 2020, 2021, 2022, 2023]


In [29]:
images = years.map(best_image)

In [34]:
count = images.size().getInfo()
print(count)

11


In [31]:
ee.ImageCollection(images).aggregate_array("CLOUD_COVER").getInfo()

[0, 0, 0.01, 0, 0, 0, 0.01, 0.09, 0, 0, 0]

In [35]:
ee.ImageCollection(images).aggregate_array("system:id").getInfo()

['LANDSAT/LC08/C02/T1_L2/LC08_202034_20130724',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20140812',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20150730',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20160801',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20170804',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20180924',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20190810',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20201031',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20210730',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20220818',
 'LANDSAT/LC08/C02/T1_L2/LC08_202034_20230805']

In [ ]:
for index in range(0, count):
    image = ee.Image(images.get(index))
    layer_name = "Image " + str(year_list[index])
    print(layer_name)
    Map.addLayer(image, vis_params, layer_name, False)

Image 2013
Image 2014
Image 2015
Image 2016
Image 2017


In [36]:
Map = geemap.Map(height=1200)
Map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

## Set image properties

In [40]:
collection = ee.ImageCollection(images)

In [41]:
collection.aggregate_array("system:time_start").getInfo()

[1374663871573,
 1407841356543,
 1438254130356,
 1470049354514,
 1501844552565,
 1537786934036,
 1565434959955,
 1604142172552,
 1627642956011,
 1660820585347,
 1691233344928]

In [42]:
collection = collection.map(lambda img: img.set({"DATE": ee.Date(img.get("system:time_start")).format("YYYY-MM-dd")}))

In [43]:
collection.aggregate_array("DATE").getInfo()

['2013-07-24',
 '2014-08-12',
 '2015-07-30',
 '2016-08-01',
 '2017-08-04',
 '2018-09-24',
 '2019-08-10',
 '2020-10-31',
 '2021-07-30',
 '2022-08-18',
 '2023-08-05']

# <font color='red'>**GEE Lesson 13 - Visualizing Earth Engine time-series images**</font>


https://tutorials.geemap.org/ImageCollection/visualizing_time_series/

## Visualizing weather data

In [46]:
Map = geemap.Map()

collection = ee.ImageCollection('NOAA/GFS0P25') \
  .filterDate('2021-07-22', '2021-07-23') \
  .limit(24) \
  .select('temperature_2m_above_ground')

vis_params = {
  'min': -40.0,
  'max': 35.0,
  'palette': ['blue', 'purple', 'cyan', 'green', 'yellow', 'red']
}

first_image = collection.first()

Map.addLayer(first_image, vis_params, "First image")
Map.setCenter(-0.3490, 25.7900, 2)
Map

Map(center=[25.79, -0.349], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataG…

#<font color = 'red'>**GEE Lesson 14 - Exporting Earth Engine data**</font>


https://tutorials.geemap.org/AssetManagement/export_data/

In [56]:
import os
from geemap.datasets import DATA

In [57]:
Map = geemap.Map()

## Set an output directory

In [58]:
out_dir = os.path.expanduser("~/Downloads")

if not os.path.exists(out_dir):
    os.makedirs(out_dir)

In [59]:
out_dir = os.path.expanduser("~/Downloads")
filename = os.path.join(out_dir, 'landsat.tif')
print(filename)

/root/Downloads/landsat.tif


## Export an ee.FeatureCollection

In [60]:
fc = ee.FeatureCollection('users/giswqs/public/countries')

In [61]:
Map.addLayer(fc, {}, "Countries")
Map.centerObject(fc)
Map

Map(center=[0, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=SearchDataGUI(childr…

Export data to a local computer

In [62]:
out_shp = os.path.join(out_dir, "countries.shp")
geemap.ee_export_vector(fc, out_shp, verbose=True)

Generating URL ...
Please wait ...
An error occurred while downloading. 
 Retrying ...
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/countries.shp


Export data to Google Drive

In [ ]:
geemap.ee_export_vector_to_drive(fc, description="countries", folder="export")

Exporting countries...


## Export an ee.Image

In [ ]:
image = ee.Image('LE7_TOA_5YEAR/1999_2003')

landsat_vis = {
    'bands': ['B4', 'B3', 'B2'],
    'gamma': 1.7
}
Map.addLayer(image, landsat_vis, "LE7_TOA_5YEAR/1999_2003", True, 1)
Map

Map(bottom=536.0, center=[14.016649062891737, 0.0], controls=(WidgetControl(options=['position', 'transparent_…

In [ ]:
out_dir = os.path.expanduser("~/Downloads")
filename = os.path.join(out_dir, 'landsat.tif')
#print(filename)

### Exporting all bands as one single image

In [ ]:
# Draw any shapes on the map using the Drawing tools before executing this code block
roi = Map.user_roi

In [ ]:
roi.getInfo()

{'type': 'Polygon',
 'coordinates': [[[-366.816148, 36.752289],
   [-365.887284, 36.752289],
   [-365.887284, 37.572091],
   [-366.816148, 37.572091],
   [-366.816148, 36.752289]]]}

In [ ]:
image_clip = image.clip(roi)

In [ ]:
Map.addLayer(image_clip, landsat_vis, "image")

In [ ]:
geemap.ee_export_image(image_clip, filename=filename, scale=90, region=roi, file_per_band=False)

Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/landsat.tif


### Exporting each band as one image

In [ ]:
geemap.ee_export_image(image, filename=filename, scale=90, region=roi, file_per_band=True)

Generating URL ...
Please wait ...
Data downloaded to /root/Downloads


### Export an image to Google Drive

In [ ]:
geemap.ee_export_image_to_drive(image_clip, description='landsat', folder='export', region=roi, scale=30)

Exporting landsat ...


## Download an ee.ImageCollection

In [ ]:
loc = ee.Geometry.Point(-99.2222, 46.7816)
collection = ee.ImageCollection('USDA/NAIP/DOQQ') \
    .filterBounds(loc) \
    .filterDate('2008-01-01', '2020-01-01') \
    .filter(ee.Filter.listContains("system:band_names", "N"))

In [ ]:
out_dir = os.path.expanduser('~/Downloads')

In [ ]:
collection.aggregate_array('system:index').getInfo()

['m_4609915_sw_14_060_20180902_20181213',
 'm_4609915_sw_14_060_20190626',
 'm_4609915_sw_14_1_20090818',
 'm_4609915_sw_14_1_20100629',
 'm_4609915_sw_14_1_20120714',
 'm_4609915_sw_14_1_20140901',
 'm_4609915_sw_14_1_20150926',
 'm_4609915_sw_14_h_20160704',
 'm_4609915_sw_14_h_20170703']

In [ ]:
geemap.ee_export_image_collection(collection, scale=5, out_dir=out_dir)

Total number of images: 9

Exporting 1/9: m_4609915_sw_14_060_20180902_20181213.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_060_20180902_20181213.tif


Exporting 2/9: m_4609915_sw_14_060_20190626.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_060_20190626.tif


Exporting 3/9: m_4609915_sw_14_1_20090818.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_1_20090818.tif


Exporting 4/9: m_4609915_sw_14_1_20100629.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_1_20100629.tif


Exporting 5/9: m_4609915_sw_14_1_20120714.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_1_20120714.tif


Exporting 6/9: m_4609915_sw_14_1_20140901.tif
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/m_4609915_sw_14_1_20140901.tif


Exporting 7/9: m_4609915_sw_14_1_20150926.tif
Generat

In [ ]:
geemap.ee_export_image_collection_to_drive(collection, folder='export', scale=10)

Total number of images: 9

Exporting m_4609915_sw_14_060_20180902_20181213 ...
Exporting m_4609915_sw_14_060_20190626 ...
Exporting m_4609915_sw_14_1_20090818 ...
Exporting m_4609915_sw_14_1_20100629 ...
Exporting m_4609915_sw_14_1_20120714 ...
Exporting m_4609915_sw_14_1_20140901 ...
Exporting m_4609915_sw_14_1_20150926 ...
Exporting m_4609915_sw_14_h_20160704 ...
Exporting m_4609915_sw_14_h_20170703 ...


## Extract pixels as a Numpy array

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

img = ee.Image('LANDSAT/LC08/C01/T1_SR/LC08_038029_20180810') \
  .select(['B4', 'B5', 'B6'])

aoi = ee.Geometry.Polygon(
  [[[-110.8, 44.7],
    [-110.8, 44.6],
    [-110.6, 44.6],
    [-110.6, 44.7]]], None, False)

rgb_img = geemap.ee_to_numpy(img, region=aoi)
print(rgb_img.shape)

(373, 531, 3)


# <font color = 'red'>**GEE Lesson 16 - Extracting time-series pixel values from Earth Engine Image**</font>


https://tutorials.geemap.org/AssetManagement/extract_values/

In [ ]:
Map = geemap.Map()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [ ]:
landsat7 = ee.Image('LE7_TOA_5YEAR/1999_2003') \
    .select([0, 1, 2, 3, 4, 6])
landsat_vis = {
    'bands': ['B4', 'B3', 'B2'],
    'gamma': 1.7
}
Map.addLayer(landsat7, landsat_vis, "LE7_TOA_5YEAR/1999_2003")

Map.set_plot_options(add_marker_cluster=True)

### Export pixel values to shapefile/csv

In [ ]:
out_dir = os.path.expanduser('~/Downloads')
# out_csv = os.path.join(out_dir, 'points.csv')
out_shp = os.path.join(out_dir, 'points.shp')
print(out_shp)

/root/Downloads/points.shp


In [ ]:
Map.extract_values_to_points(out_shp)

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


## Interactive Region Reduction

In [ ]:
import geemap.colormaps as cm

In [ ]:
m = geemap.Map()

In [ ]:
collection = ee.ImageCollection('MODIS/006/MOD13A2') \
    .filterDate('2015-01-01', '2019-12-31') \
    .select('NDVI')

# Convert the image collection to an image.
image = collection.toBands()

palette = cm.palettes.ndvi

ndvi_vis = {
  'min': 0.0,
  'max': 9000.0,
  'palette': palette
}

m.addLayer(image, {}, 'MODIS NDVI Time-series')
m.addLayer(image.select(0), ndvi_vis, 'MODIS NDVI VIS')

m

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [ ]:
m.set_plot_options(add_marker_cluster=True, marker=None)
m.roi_reducer = ee.Reducer.mean()

### Export data

In [ ]:
out_dir = os.path.expanduser('~/Downloads')
# out_csv = os.path.join(out_dir, 'points.csv')
out_shp = os.path.join(out_dir, 'ndvi.shp')
m.extract_values_to_points(out_shp)

## Creating training samples

In [ ]:
geemap.show_youtube("https://youtu.be/VWh5PxXPZw0")

Output(layout=Layout(width='815px'))

In [ ]:
Map = geemap.Map()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [ ]:
Map.user_rois.getInfo()

In [ ]:
out_dir = os.path.expanduser('~/Downloads')
out_shp = os.path.join(out_dir, 'collections_sample.shp')

In [ ]:
geemap.ee_to_shp(Map.user_rois, out_shp)

Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/collections_sample.shp


## <font color = 'red'>**GEE Lesson 18. Computing zonal statistics with Google Earth Engine**</font>

https://tutorials.geemap.org/Analysis/zonal_statistics/

In [ ]:
Map = geemap.Map()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

In [ ]:
# Add Earth Engine dataset
dem = ee.Image('USGS/SRTMGL1_003')

# Set visualization parameters.
dem_vis = {
  'min': 0,
  'max': 4000,
  'palette': ['006633', 'E5FFCC', '662A00', 'D8D8D8', 'F5F5F5']}

# Add Earth Engine DEM to map
Map.addLayer(dem, dem_vis, 'SRTM DEM')

# Add Landsat data to map
landsat = ee.Image('LE7_TOA_5YEAR/1999_2003')

landsat_vis = {
    'bands': ['B4', 'B3', 'B2'],
    'gamma': 1.4
}
Map.addLayer(landsat, landsat_vis, "Landsat", False)

Map.addLayer(fc, {}, 'countries')

## Compute zonal statistics for one image

In [ ]:
out_dir = os.path.expanduser('~/Downloads')
if not os.path.exists(out_dir):
    os.makedirs(out_dir)

In [ ]:
out_dem_stats = os.path.join(out_dir, 'dem_stats.csv')

# Allowed output formats: csv, shp, json, kml, kmz
# Allowed statistics type: MEAN, MAXIMUM, MINIMUM, MEDIAN, STD, MIN_MAX, VARIANCE, SUM
geemap.zonal_statistics(dem, fc, out_dem_stats, statistics_type='MEAN', scale=1000)

Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/dem_stats.csv


In [ ]:
out_landsat_stats = os.path.join(out_dir, 'landsat_stats.csv')
geemap.zonal_statistics(landsat, states, out_landsat_stats, statistics_type='SUM', scale=1000)

## Compute zonal statistics for time-series images

In [ ]:
Map = geemap.Map()

collection = ee.ImageCollection('MODIS/MCD43A4_006_NDVI') \
                  .filter(ee.Filter.date('2018-04-01', '2018-05-01')) \
                  .select("NDVI")\

vis_params = {
  'min': 0.0,
  'max': 1.0,
  'palette': [
    'FFFFFF', 'CE7E45', 'DF923D', 'F1B555', 'FCD163', '99B718', '74A901',
    '66A000', '529400', '3E8601', '207401', '056201', '004C00', '023B01',
    '012E01', '011D01', '011301'
  ],
}

first_image = collection.first()

Map.addLayer(first_image, vis_params, "First image")
Map.setCenter(-7.03125, 31.0529339857, 2)
Map

Map(center=[31.0529339857, -7.03125], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=H…

In [ ]:
modis = collection.toBands()
Map.addLayer(modis, {}, "MODIS Time series", False)

In [ ]:
out_landsat_stats = os.path.join(out_dir, 'ndvi.csv')
geemap.zonal_statistics(modis, fc, out_landsat_stats, statistics_type='MEAN', scale=1000)

Computing statistics ...
Generating URL ...


Please wait ...
Data downloaded to /root/Downloads/ndvi.csv


In [ ]:
out_landsat_stats = os.path.join(out_dir, 'ndvi.csv')
geemap.zonal_statistics(modis, fc, out_landsat_stats, statistics_type='MEAN', scale=1000)

Computing statistics ...
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/ndvi.csv


# <font color = 'red'>**GEE Lesson 19 - Computing zonal statistics by group with Google Earth Engine**</font>

https://tutorials.geemap.org/Analysis/zonal_stats_by_group/

In [ ]:
Map = geemap.Map()
Map

Map(center=[20, 0], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(children=(Togg…

### Add NLCD data

NLCD: USGS National Land Cover Database

https://developers.google.com/earth-engine/datasets/catalog/USGS_NLCD_RELEASES_2016_REL

In [ ]:
dataset = ee.Image('USGS/NLCD/NLCD2016')
landcover = ee.Image(dataset.select('landcover'))
Map.addLayer(landcover, {}, 'NLCD 2016')

states = ee.FeatureCollection("TIGER/2018/States")
Map.addLayer(states, {}, 'US States')

In [ ]:
Map.add_legend(builtin_legend='NLCD')

### Calculate land cover compostion of each US state

In [ ]:
out_dir = os.path.expanduser('~/Downloads')
if not os.path.exists(out_dir):
    os.makedirs(out_dir)

In [ ]:
nlcd_stats = os.path.join(out_dir, 'nlcd_stats_sum.csv')

# statistics_type can be either 'SUM' or 'PERCENTAGE'
# denominator can be used to convert square meters to other areal units, such as square kilimeters
geemap.zonal_statistics_by_group(landcover, states, nlcd_stats, statistics_type='SUM', denominator=1000000, decimal_places=2)

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/nlcd_stats_sum.csv


In [ ]:
nlcd_stats = os.path.join(out_dir, 'nlcd_stats_pct.csv')
geemap.zonal_statistics_by_group(landcover, states, nlcd_stats, statistics_type='PERCENTAGE')

## Analyzing Global Land Cover

### Add MODIS global land cover data

MCD12Q1.006 MODIS Land Cover Type Yearly Global 500m

https://developers.google.com/earth-engine/datasets/catalog/MODIS_006_MCD12Q1

In [ ]:
Map = geemap.Map()

landcover = ee.Image('MODIS/006/MCD12Q1/2019_01_01') \
    .select('LC_Type1')

igbpLandCoverVis = {
  'min': 1.0,
  'max': 17.0,
  'palette': [
    '05450a', '086a10', '54a708', '78d203', '009900', 'c6b044', 'dcd159',
    'dade48', 'fbff13', 'b6ff05', '27ff87', 'c24f44', 'a5a5a5', 'ff6d4c',
    '69fff8', 'f9ffa4', '1c0dff'
  ],
}

Map.setCenter(6.746, 46.529, 2)
Map.addLayer(landcover, igbpLandCoverVis, 'MODIS Land Cover')

countries = ee.FeatureCollection('users/giswqs/public/countries')
Map.addLayer(countries, {}, "Countries")

Map

Map(center=[46.529, 6.746], controls=(WidgetControl(options=['position', 'transparent_bg'], widget=HBox(childr…

In [ ]:
Map.add_legend(builtin_legend='MODIS/051/MCD12Q1')

In [ ]:
out_dir = os.path.join(os.path.expanduser('~'), 'Downloads')
global_stats = os.path.join(out_dir, 'global_stats_sum.csv')

# statistics_type can be either 'SUM' or 'PERCENTAGE'
# denominator can be used to convert square meters to other areal units, such as square kilimeters
geemap.zonal_statistics_by_group(landcover, countries, global_stats, statistics_type='SUM', denominator=1000000, decimal_places=2)

Computing ... 
Generating URL ...
Please wait ...
Data downloaded to /root/Downloads/global_stats_sum.csv
